# Использование API в открытом доступе. Hotellook
Ссылка на сайт: https://search.hotellook.com/

In [2]:
import requests
import json

Переходим на страницу [с отелями в Москве](https://search.hotellook.com/hotels?=1&cityId=12153), указываем любые параметры заселения. Изначально мы планировали получить информацию из сайта методом парсинга, после изучения исходного кода главной страницы и отдельной страницы для конкретного отеля было выявлено, что даже если на если полученных html можно получить информацию, то она не будет особо полезной, а затраты на парсинг плохо структурированных html будут крайне велики.

После данного вывода, было решено рассмотреть внешние запросы, которые сайт делает во время загрузки. С помощью панели "Сеть" в инструментах разработчика браузера Microsoft Edge был найден интересный запрос на адрес https://search.hotellook.com/api/wl_search/result Название сайта сразу же привлекло наше внимание, поэтому мы решили скопировать запрос в виде curl (пример запроса смотри ниже), чтобы проверить, поможет ли данная находка в сборе информации. 

```bash
curl 'https://search.hotellook.com/api/wl_search/result' \
  -H 'accept: */*' \
  -H 'accept-language: ru,en;q=0.9,en-GB;q=0.8,en-US;q=0.7' \
  -H 'content-type: application/json' \
  -b '_ym_uid=1740687636891539769; _ym_d=1740687636; _ym_isad=2; _fbp=fb.1.1740687635990.94303087349110335; _ym_visorc=w; locale=en; currency=RUB; _sp_ses.b93a=*; SERVERID=s1; hide_hotels=true; marker=direct.Zzf9414da07bac412a8081a93-126017; hotel_search_params=%7B%22params_attributes%22%3A%7B%22check_in%22%3A%222025-03-06%22%2C%22check_out%22%3A%222025-03-13%22%2C%22destination%22%3A%7B%22name%22%3A%22Moscow%22%2C%22location_id%22%3A12153%7D%7D%7D; __gads=ID=44dcaed736b18c79:T=1740690590:RT=1740690590:S=ALNI_MZXwNbPSlTOoNneAx98XOLGWMR8Tg; __gpi=UID=00001047f9069e5d:T=1740690590:RT=1740690590:S=ALNI_MavMYFmwoZLswhjRNWA5OEp3F6L2w; __eoi=ID=b27dad9016678eb9:T=1740690590:RT=1740690590:S=AA-AfjZC8WTywdSjZyrYKFv1Ea1G; _sp_id.b93a=0645083f-b576-46c5-ad0e-2bab35cc307c.1740687637.1.1740690593.1740687637.0c51d766-a433-4071-8ee4-45b25167c7f0' \
  -H 'origin: https://search.hotellook.com' \
  -H 'priority: u=1, i' \
  -H 'referer: https://search.hotellook.com/hotels?=1&adults=2&checkIn=2025-03-06&checkOut=2025-03-13&children=&cityId=12153&currency=rub&destination=Moscow&language=en&marker=direct.Zzf9414da07bac412a8081a93-126017' \
  -H 'sec-ch-ua: "Not(A:Brand";v="99", "Microsoft Edge";v="133", "Chromium";v="133"' \
  -H 'sec-ch-ua-mobile: ?0' \
  -H 'sec-ch-ua-platform: "Windows"' \
  -H 'sec-fetch-dest: empty' \
  -H 'sec-fetch-mode: cors' \
  -H 'sec-fetch-site: same-origin' \
  -H 'user-agent: Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/133.0.0.0 Safari/537.36 Edg/133.0.0.0' \
  --data-raw '{"page":"serp","search_id":"23882775-d9cb-466e-8077-68984e8b2c3f","params":{"check_in":"2025-03-06","check_out":"2025-03-13","marker":"direct.Zzf9414da07bac412a8081a93-126017","currency":"rub","locale":"en","rooms":[{"adults":2,"children":[]}],"locations_ids":[12153],"hotels_ids":[],"destination":"Moscow","host":"search.hotellook.com","flags":{"auid":null,"ab":null,"deviceType":"mobile"},"popularity":"default"},"selected_hotels_ids":[],"filters":{"prices":{"groups":[0,500,1000,1500,2000,2500,3000,4000,5000,6000,7000,8000,9000,12000,15000,20000,30000,50000,100000,2147483647]},"ratings":{"groups":[0,0.5,1,1.5,2,2.5,3,3.5,4,4.5,5,5.5,6,6.5,7,7.5,8,8.5,9,9.5,10]}},"sort":"popularity","limit":10,"offset":0}'
```

Помимо самого запросов и сопровождающих заголовков можно заметить "сырые данные" data-raw, это параметры запроса к API hotellook. Параметры указаны в виде JSON-данных. Мы можем воссоздать такой же запрос с помощью питона, используя библиотеку requests. Заодно уберем лишние заголовки и параметры, без которых запрос не изменится

In [45]:
def get_all_hotellook_data(limit):
    url = "https://search.hotellook.com/api/wl_search/result"
    
    headers = {
        "accept": "*/*",
        "accept-language": "ru,en;q=0.9,en-GB;q=0.8,en-US;q=0.7",
        "content-type": "application/json",
        "origin": "https://search.hotellook.com",
        "priority": "u=1, i",
        "referer": "https://search.hotellook.com/hotels?=1&cityId=12153",
        "user-agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/133.0.0.0 Safari/537.36 Edg/133.0.0.0"
    }
    
    payload = {
        "page": "serp",
        "search_id": "",
        "params": {
            "check_in": "2025-02-28",
            "check_out": "2025-03-01",
            "currency": "rub",
            "locale": "ru",
            "rooms": [{"adults": 2, "children": []}],
            "locations_ids": [12153],
            "destination": None,
            "hotels_ids": [],
            "host": "search.hotellook.com",
            "flags": {"auid": None, "ab": None, "deviceType": "mobile"},
            "popularity": "default"
        },
        "sort": "popularity",
        "limit": limit,
        "offset": 0
    }
    
    response = requests.post(url, headers=headers, json=payload)
    return response


In [46]:
response = get_all_hotellook_data(limit=3)
data = response.json()

# Печатаем в удобном для просмотра виде
print(json.dumps(data, indent=4, ensure_ascii=False))

{
    "search_id": "e13514f9-99f6-42f2-bb84-c924dea0066c",
    "stop": false,
    "locations": {
        "12153": {
            "seasons": {},
            "name": "Москва",
            "country_name": "Россия",
            "country_id": 186,
            "declensions": {
                "1": "Москва",
                "2": "Москвы",
                "3": "Москве",
                "4": "Москву",
                "5": "Москвой",
                "6": "Москве",
                "7": "в Москве"
            },
            "property_types_count": {
                "by_types": {
                    "0": 37,
                    "1": 670,
                    "2": 18,
                    "3": 5,
                    "4": 1633,
                    "5": 1,
                    "6": 28,
                    "7": 109
                },
                "total": 2501
            },
            "timezone": "Europe/Moscow",
            "iatas": [],
            "center_coords": {
                "lat": 55.75204,


Запрос на всего три отеля выдал JSON в 500 строк. В данном response уже есть полезные данные, которые затем будут использованы в проекте (TODO - Саша, напиши подробно, какая информация будет использоваться из JSON). При этом логично будет предположить, что на отдельной странице конкретного отеля будет еще больше подробной информации. Таким образом, повторим действия описанные ранее и создадим запрос для получения информации о конкретном отеле.   

In [42]:
import requests
import json

single_hotel_url = "https://search.hotellook.com/api/wl_search/result"
hotel_id_1 = 1898005746  # Pokrovka
hotel_id_2 = 333572  # Borodino

single_hotel_headers = {
    "accept": "*/*",
    "accept-language": "ru,en;q=0.9,en-GB;q=0.8,en-US;q=0.7",
    "content-type": "application/json",
    "origin": "https://search.hotellook.com",
    "user-agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/133.0.0.0 Safari/537.36 Edg/133.0.0.0"
}

single_hotel_payload = {
    "page": "hotel_page",
    "search_id": "7c33f3c5-37ab-4ead-88c4-84c31e121e33",
    "params": {
        "marker": "direct.Zz1f6b911e8a60403ca251d64-126017",
        "currency": "rub",
        "locale": "ru",
        "locations_ids": [],
        "hotels_ids": [hotel_id_2],
        "host": "search.hotellook.com",
        "flags": {"auid": None, "ab": None, "deviceType": "desktop"},
        "popularity": "default"
    },
    "selected_hotels_ids": [],
    "filters": {},
    "sort": "popularity",
    "limit": 1,
    "offset": 0
}

response = requests.post(single_hotel_url, headers=single_hotel_headers, json=single_hotel_payload)
print(response.status_code)


200


In [43]:
data_hotel = response.json()
print(json.dumps(data_hotel, indent=4, ensure_ascii=False))

{
    "search_id": "",
    "stop": true,
    "locations": {
        "12153": {
            "seasons": {},
            "name": "Москва",
            "country_name": "Россия",
            "country_id": 186,
            "declensions": {
                "1": "Москва",
                "2": "Москвы",
                "3": "Москве",
                "4": "Москву",
                "5": "Москвой",
                "6": "Москве",
                "7": "в Москве"
            },
            "property_types_count": {
                "by_types": {
                    "0": 37,
                    "1": 670,
                    "2": 18,
                    "3": 5,
                    "4": 1633,
                    "5": 1,
                    "6": 28,
                    "7": 109
                },
                "total": 2501
            },
            "timezone": "Europe/Moscow",
            "iatas": [],
            "center_coords": {
                "lat": 55.75204,
                "lon": 37.617508
    

TODO - сделать вывод, различаются ли данные во время представления их в виде общего запроса и в виде отдельного запроса (предполагаю, что нет, но надо убедиться)

Начнем полноценно выкачивать данные из API, настроив limit на максимальное количество доступных отелей - 9163 (указано на сайте)

In [47]:
# TODO - поменять на 9163 
response = get_all_hotellook_data(limit=1000)
data = response.json()

print(json.dumps(data, indent=4, ensure_ascii=False))

{
    "search_id": "00569591-3a07-48ff-b907-cb3693900cff",
    "stop": false,
    "locations": {
        "12153": {
            "seasons": {},
            "name": "Москва",
            "country_name": "Россия",
            "country_id": 186,
            "declensions": {
                "1": "Москва",
                "2": "Москвы",
                "3": "Москве",
                "4": "Москву",
                "5": "Москвой",
                "6": "Москве",
                "7": "в Москве"
            },
            "property_types_count": {
                "by_types": {
                    "0": 37,
                    "1": 670,
                    "2": 18,
                    "3": 5,
                    "4": 1633,
                    "5": 1,
                    "6": 28,
                    "7": 109
                },
                "total": 2501
            },
            "timezone": "Europe/Moscow",
            "iatas": [],
            "center_coords": {
                "lat": 55.75204,


In [48]:
# Далее необходимо полученный json преобразовать в df и отправить его на базовый EDA